# Challenge 2: Sentiment Analysis

In this challenge we will learn sentiment analysis and practice performing sentiment analysis on Twitter tweets. 

## Introduction

Sentiment analysis is to *systematically identify, extract, quantify, and study affective states and subjective information* based on texts ([reference](https://en.wikipedia.org/wiki/Sentiment_analysis)). In simple words, it's to understand whether a person is happy or unhappy in producing the piece of text. Why we (or rather, companies) care about sentiment in texts? It's because by understanding the sentiments in texts, we will be able to know if our customers are happy or unhappy about our products and services. If they are unhappy, the subsequent action is to figure out what have caused the unhappiness and make improvements.

Basic sentiment analysis only understands the *positive* or *negative* (sometimes *neutral* too) polarities of the sentiment. More advanced sentiment analysis will also consider dimensions such as agreement, subjectivity, confidence, irony, and so on. In this challenge we will conduct the basic positive vs negative sentiment analysis based on real Twitter tweets.

NLTK comes with a [sentiment analysis package](https://www.nltk.org/api/nltk.sentiment.html). This package is great for dummies to perform sentiment analysis because it requires only the textual data to make predictions. For example:

```python
>>> from nltk.sentiment.vader import SentimentIntensityAnalyzer
>>> txt = "Ironhack is a Global Tech School ranked num 2 worldwide.   Our mission is to help people transform their careers and join a thriving community of tech professionals that love what they do."
>>> analyzer = SentimentIntensityAnalyzer()
>>> analyzer.polarity_scores(txt)
{'neg': 0.0, 'neu': 0.741, 'pos': 0.259, 'compound': 0.8442}
```

In this challenge, however, you will not use NLTK's sentiment analysis package because in your Machine Learning training in the past 2 weeks you have learned how to make predictions more accurate than that. The [tweets data](https://www.kaggle.com/kazanova/sentiment140) we will be using today are already coded for the positive/negative sentiment. You will be able to use the Naïve Bayes classifier you learned in the lesson to predict the sentiment of tweets based on the labels.

## Conducting Sentiment Analysis

### Loading and Exploring Data

The dataset we'll be using today is located on Kaggle (https://www.kaggle.com/kazanova/sentiment140). Once you have downloaded and imported the dataset, it you will need to define the columns names: df.columns = ['target','id','date','flag','user','text']

*Notes:* 

* The dataset is huuuuge (1.6m tweets). When you develop your data analysis codes, you can sample a subset of the data (e.g. 20k records) so that you will save a lot of time when you test your codes.

In [1]:
import pandas as pd
import nltk
from nltk.stem import WordNetLemmatizer, PorterStemmer
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk import FreqDist
import re

In [2]:
df = pd.read_csv('training.1600000.processed.noemoticon.csv', encoding='latin-1')
df.columns = ['target','id','date','flag','user','text']
df.head()

subset_size = 20000

df = df.sample(n=subset_size)

### Prepare Textual Data for Sentiment Analysis

Now, apply the functions you have written in Challenge 1 to your whole data set. These functions include:

* `clean_up()`

* `tokenize()`

* `stem_and_lemmatize()`

* `remove_stopwords()`

Create a new column called `text_processed` in the dataframe to contain the processed data. At the end, your `text_processed` column should contain lists of word tokens that are cleaned up. Your data should look like below:

![Processed Data](data-cleaning-results.png)

In [3]:
def clean_up(s):
    """
    Cleans up numbers, URLs, and special characters from a string.

    Args:
        s: The string to be cleaned up.

    Returns:
        A string that has been cleaned up.
    """

    text_no_numbers = re.sub('\d', ' ', s)
    text_no_url = re.sub(r'http[s]?://\S+', ' ', text_no_numbers)
    cleaned_text = re.sub(r'[^a-zA-Z\s]', ' ', text_no_url)
    return cleaned_text.lower()

def tokenize(s):
    """
    Tokenize a string.

    Args:
        s: String to be tokenized.

    Returns:
        A list of words as the result of tokenization.
    """
    tokens = word_tokenize(s)
    return tokens

def stem_and_lemmatize(l):
    """
    Perform stemming and lemmatization on a list of words.

    Args:
        l: A list of strings.

    Returns:
        A list of strings after being stemmed and lemmatized.
    """
    stemmer = PorterStemmer()
    lemmatizer = WordNetLemmatizer()
    stemmed_words = [stemmer.stem(word) for word in l]
    lemmatized_words = [lemmatizer.lemmatize(word) for word in stemmed_words]


    return lemmatized_words

def remove_stopwords(l):
    """
    Remove English stopwords from a list of strings.

    Args:
        l: A list of strings.

    Returns:
        A list of strings after stop words are removed.
    """
    stopwords_list = stopwords.words('english')

    for word in l:
        if word in stopwords_list:
            l.remove(word)    
    return l

In [4]:
from tqdm import tqdm # cool library which can save your sanity
tqdm.pandas()
df['text_cleanup'] = df['text'].progress_apply(clean_up)
df[['text', 'text_cleanup']]

100%|████████████████████████████████████████████████████████████████████████| 20000/20000 [00:00<00:00, 195731.64it/s]


text  \
104614                              He's kinda mad though    
858292                                   enjoying the day    
563466   working so hard  , these days im so busy ... i...   
57829                        Gnite twitter! Work in 5 hrs    
1434987                           @raniinsight : hey rani    
...                                                    ...   
618055   plans always get screwed up!! grrr!! wish jaso...   
641999   my f-ing everything hurts...didnt sleep all ni...   
254810                             @sloppyness work blows    
195848   Where are my hommies? @mykurs, @redhotchillime...   
741719   HAPPY FATHER'S DAY, Daddy!! I know you're with...   

                                              text_cleanup  
104614                              he s kinda mad though   
858292                                   enjoying the day   
563466   working so hard    these days im so busy     i...  
57829                        gnite twitter  work in   hrs   
1434987                            raniinsight   hey rani   
...                                                    ...  
618055   plans always get screwed up   grrr   wish jaso...  
641999   my f ing everything hurts   didnt sleep all ni...  
254810                              sloppyness work blows   
195848   where are my hommies   mykurs   redhotchillime...  
741719   happy father s day  daddy   i know you re with...  

[20000 rows x 2 columns]

In [5]:
df['text_tokenize'] = df['text_cleanup'].progress_apply(tokenize)
df[['text', 'text_tokenize']]

100%|█████████████████████████████████████████████████████████████████████████| 20000/20000 [00:01<00:00, 13880.90it/s]


text  \
104614                              He's kinda mad though    
858292                                   enjoying the day    
563466   working so hard  , these days im so busy ... i...   
57829                        Gnite twitter! Work in 5 hrs    
1434987                           @raniinsight : hey rani    
...                                                    ...   
618055   plans always get screwed up!! grrr!! wish jaso...   
641999   my f-ing everything hurts...didnt sleep all ni...   
254810                             @sloppyness work blows    
195848   Where are my hommies? @mykurs, @redhotchillime...   
741719   HAPPY FATHER'S DAY, Daddy!! I know you're with...   

                                             text_tokenize  
104614                         [he, s, kinda, mad, though]  
858292                                [enjoying, the, day]  
563466   [working, so, hard, these, days, im, so, busy,...  
57829                      [gnite, twitter, work, in, hrs]  
1434987                           [raniinsight, hey, rani]  
...                                                    ...  
618055   [plans, always, get, screwed, up, grrr, wish, ...  
641999   [my, f, ing, everything, hurts, didnt, sleep, ...  
254810                           [sloppyness, work, blows]  
195848   [where, are, my, hommies, mykurs, redhotchilli...  
741719   [happy, father, s, day, daddy, i, know, you, r...  

[20000 rows x 2 columns]

In [6]:
df['text_stem'] = df['text_tokenize'].progress_apply(stem_and_lemmatize)
df[['text', 'text_stem']]

100%|██████████████████████████████████████████████████████████████████████████| 20000/20000 [00:08<00:00, 2465.70it/s]


text  \
104614                              He's kinda mad though    
858292                                   enjoying the day    
563466   working so hard  , these days im so busy ... i...   
57829                        Gnite twitter! Work in 5 hrs    
1434987                           @raniinsight : hey rani    
...                                                    ...   
618055   plans always get screwed up!! grrr!! wish jaso...   
641999   my f-ing everything hurts...didnt sleep all ni...   
254810                             @sloppyness work blows    
195848   Where are my hommies? @mykurs, @redhotchillime...   
741719   HAPPY FATHER'S DAY, Daddy!! I know you're with...   

                                                 text_stem  
104614                         [he, s, kinda, mad, though]  
858292                                   [enjoy, the, day]  
563466   [work, so, hard, these, day, im, so, busi, i, ...  
57829                       [gnite, twitter, work, in, hr]  
1434987                           [raniinsight, hey, rani]  
...                                                    ...  
618055   [plan, alway, get, screw, up, grrr, wish, jaso...  
641999   [my, f, ing, everyth, hurt, didnt, sleep, all,...  
254810                                [sloppy, work, blow]  
195848   [where, are, my, hommi, mykur, redhotchillim, ...  
741719   [happi, father, s, day, daddi, i, know, you, r...  

[20000 rows x 2 columns]

In [7]:
df['text_processed'] = df['text_stem'].progress_apply(remove_stopwords)
df[['text', 'text_processed']]

100%|██████████████████████████████████████████████████████████████████████████| 20000/20000 [00:04<00:00, 4487.56it/s]


text  \
104614                              He's kinda mad though    
858292                                   enjoying the day    
563466   working so hard  , these days im so busy ... i...   
57829                        Gnite twitter! Work in 5 hrs    
1434987                           @raniinsight : hey rani    
...                                                    ...   
618055   plans always get screwed up!! grrr!! wish jaso...   
641999   my f-ing everything hurts...didnt sleep all ni...   
254810                             @sloppyness work blows    
195848   Where are my hommies? @mykurs, @redhotchillime...   
741719   HAPPY FATHER'S DAY, Daddy!! I know you're with...   

                                            text_processed  
104614                             [s, kinda, mad, though]  
858292                                        [enjoy, day]  
563466   [work, hard, day, im, busi, have, lot, thing, do]  
57829                           [gnite, twitter, work, hr]  
1434987                           [raniinsight, hey, rani]  
...                                                    ...  
618055   [plan, alway, get, screw, grrr, wish, jason, g...  
641999        [f, ing, everyth, hurt, didnt, sleep, night]  
254810                                [sloppy, work, blow]  
195848   [are, hommi, mykur, redhotchillim, pattysingso...  
741719   [happi, father, day, daddi, know, re, god, sti...  

[20000 rows x 2 columns]

In [8]:
df[['text', 'text_processed']].head(20)

text  \
104614                              He's kinda mad though    
858292                                   enjoying the day    
563466   working so hard  , these days im so busy ... i...   
57829                        Gnite twitter! Work in 5 hrs    
1434987                           @raniinsight : hey rani    
1000673  @Coley81 Sweet and carbonated, just like me, lol    
238433                 Awake and Sick. Really really sick    
1305581  @SperoAmor noia! Oh dear lord. Hell no I'm gon...   
1063843  @bonasaurus why can't more people appreciate s...   
1113091                        @Emmaaaar sounds laaaavely    
1359774       @carolteodori thank god it was ALMOST, hehe    
1138196                    Just got on eBay  must have hat   
88156    sore lip, tongue, throat &amp; tooth. what nex...   
1043478  @scorpiojerm @BentoSet come to BKK to party Au...   
1062409                                Swimsuit shoppingg    
1257402  Yep. Ed.  I would totally give him a way to go...   
787759   Hopefully she'll see this at one point of toda...   
787099   @Sihuiii &quot;CROATIA LAH CROCTIA CROCTIA JIA...   
203553   @brigittepicot yes i am! but i've been so busy...   
304418   @AllShadow Lol, I'm joking, but not really. I ...   

                                            text_processed  
104614                             [s, kinda, mad, though]  
858292                                        [enjoy, day]  
563466   [work, hard, day, im, busi, have, lot, thing, do]  
57829                           [gnite, twitter, work, hr]  
1434987                           [raniinsight, hey, rani]  
1000673                  [coley, sweet, carbon, like, lol]  
238433                  [awak, sick, realli, realli, sick]  
1305581  [speroamor, noia, oh, dear, lord, hell, i, gon...  
1063843  [bonasauru, whi, t, peopl, appreci, static, type]  
1113091                          [emmaaaar, sound, laaaav]  
1359774       [carolteodori, thank, god, wa, almost, hehe]  
1138196                             [got, ebay, must, hat]  
88156    [sore, lip, tongu, throat, amp, tooth, next, h...  
1043478  [scorpiojerm, bentoset, come, bkk, parti, aug,...  
1062409                              [swimsuit, shoppingg]  
1257402  [yep, ed, would, total, give, a, way, go, he, ...  
787759   [hope, ll, see, thi, one, point, today, have, ...  
787099   [sihuiii, quot, croatia, lah, croctia, croctia...  
203553   [brigittepicot, ye, am, i, been, busi, late, t...  
304418   [allshadow, lol, m, joke, not, realli, love, s...

### Creating Bag of Words

The purpose of this step is to create a [bag of words](https://en.wikipedia.org/wiki/Bag-of-words_model) from the processed data. The bag of words contains all the unique words in your whole text body (a.k.a. *corpus*) with the number of occurrence of each word. It will allow you to understand which words are the most important features across the whole corpus.

Also, you can imagine you will have a massive set of words. The less important words (i.e. those of very low number of occurrence) do not contribute much to the sentiment. Therefore, you only need to use the most important words to build your feature set in the next step. In our case, we will use the top 5,000 words with the highest frequency to build the features.

In the cell below, combine all the words in `text_processed` and calculate the frequency distribution of all words. A convenient library to calculate the term frequency distribution is NLTK's `FreqDist` class ([documentation](https://www.nltk.org/api/nltk.html#module-nltk.probability)). Then select the top 5,000 words from the frequency distribution.

In [15]:
all_words = [word for words in df['text_processed'] for word in words]

freq_dist = FreqDist(all_words)

top_words = freq_dist.most_common(5000)

top_words

selected_words = list(freq_dist.keys())[:5000]
selected_words

['s',
 'kinda',
 'mad',
 'though',
 'enjoy',
 'day',
 'work',
 'hard',
 'im',
 'busi',
 'have',
 'lot',
 'thing',
 'do',
 'gnite',
 'twitter',
 'hr',
 'raniinsight',
 'hey',
 'rani',
 'coley',
 'sweet',
 'carbon',
 'like',
 'lol',
 'awak',
 'sick',
 'realli',
 'speroamor',
 'noia',
 'oh',
 'dear',
 'lord',
 'hell',
 'i',
 'gon',
 'na',
 'cool',
 'bonasauru',
 'whi',
 't',
 'peopl',
 'appreci',
 'static',
 'type',
 'emmaaaar',
 'sound',
 'laaaav',
 'carolteodori',
 'thank',
 'god',
 'wa',
 'almost',
 'hehe',
 'got',
 'ebay',
 'must',
 'hat',
 'sore',
 'lip',
 'tongu',
 'throat',
 'amp',
 'tooth',
 'next',
 'haha',
 'scorpiojerm',
 'bentoset',
 'come',
 'bkk',
 'parti',
 'aug',
 'hk',
 'jun',
 'at',
 'play',
 'nd',
 'friday',
 'june',
 'person',
 'invit',
 'sure',
 'wait',
 'long',
 'swimsuit',
 'shoppingg',
 'yep',
 'ed',
 'would',
 'total',
 'give',
 'a',
 'way',
 'go',
 'he',
 'gage',
 'hope',
 'll',
 'see',
 'thi',
 'one',
 'point',
 'today',
 'fun',
 'spain',
 'pip',
 'miss',
 'qq',

### Building Features

Now let's build the features. Using the top 5,000 words, create a 2-dimensional matrix to record whether each of those words is contained in each document (tweet). Then you also have an output column to indicate whether the sentiment in each tweet is positive. For example, assuming your bag of words has 5 items (`['one', 'two', 'three', 'four', 'five']`) out of 4 documents (`['A', 'B', 'C', 'D']`), your feature set is essentially:

| Doc | one | two | three | four | five | is_positive |
|---|---|---|---|---|---|---|
| A | True | False | False | True | False | True |
| B | False | False | False | True | True | False |
| C | False | True | False | False | False | True |
| D | True | False | False | False | True | False|

However, because the `nltk.NaiveBayesClassifier.train` class we will use in the next step does not work with Pandas dataframe, the structure of your feature set should be converted to the Python list looking like below:

```python
[
	({
		'one': True,
		'two': False,
		'three': False,
		'four': True,
		'five': False
	}, True),
	({
		'one': False,
		'two': False,
		'three': False,
		'four': True,
		'five': True
	}, False),
	({
		'one': False,
		'two': True,
		'three': False,
		'four': False,
		'five': False
	}, True),
	({
		'one': True,
		'two': False,
		'three': False,
		'four': False,
		'five': True
	}, False)
]
```

To help you in this step, watch the [following video](https://www.youtube.com/watch?v=-vVskDsHcVc) to learn how to build the feature set with Python and NLTK. The source code in this video can be found [here](https://pythonprogramming.net/words-as-features-nltk-tutorial/).

[![Building Features](building-features.jpg)](https://www.youtube.com/watch?v=-vVskDsHcVc)

In [17]:
def create_feature_set(document, selected_words):
    document_words = set(document)
    features = {}
    
    for word in selected_words:
        features[word] = (word in document_words)
    
    return features

feature_set = []
for index, row in df.iterrows():
    document = row['text_processed']
    sentiment = row['target']
    features = create_feature_set(document, selected_words)
    feature_set.append((features, sentiment))

for features, sentiment in feature_set:
    data = df.sample(10000)
    print(features, sentiment)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'s': True, 'kinda': False, 'mad': False, 'though': False, 'enjoy': False, 'day': False, 'work': False, 'hard': False, 'im': False, 'busi': False, 'have': False, 'lot': False, 'thing': False, 'do': False, 'gnite': False, 'twitter': False, 'hr': False, 'raniinsight': False, 'hey': False, 'rani': False, 'coley': False, 'sweet': False, 'carbon': False, 'like': False, 'lol': False, 'awak': False, 'sick': False, 'realli': False, 'speroamor': False, 'noia': False, 'oh': False, 'dear': False, 'lord': False, 'hell': False, 'i': False, 'gon': False, 'na': False, 'cool': False, 'bonasauru': False, 'whi': False, 't': False, 'peopl': False, 'appreci': False, 'static': False, 'type': False, 'emmaaaar': False, 'sound': False, 'laaaav': False, 'carolteodori': False, 'thank': False, 'god': False, 'wa': False, 'almost': False, 'hehe': False, 'got': False, 'ebay': False, 'must': False, 'hat': False, 'sore': False, 'lip': False, 'tongu': False, 'throat': False, 'amp': False, 'tooth': False, 'next': False

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'s': False, 'kinda': False, 'mad': False, 'though': False, 'enjoy': False, 'day': False, 'work': False, 'hard': False, 'im': False, 'busi': False, 'have': False, 'lot': False, 'thing': False, 'do': False, 'gnite': False, 'twitter': False, 'hr': False, 'raniinsight': False, 'hey': False, 'rani': False, 'coley': False, 'sweet': False, 'carbon': False, 'like': False, 'lol': False, 'awak': False, 'sick': False, 'realli': False, 'speroamor': False, 'noia': False, 'oh': True, 'dear': False, 'lord': False, 'hell': False, 'i': False, 'gon': False, 'na': False, 'cool': False, 'bonasauru': False, 'whi': False, 't': False, 'peopl': False, 'appreci': False, 'static': False, 'type': False, 'emmaaaar': False, 'sound': False, 'laaaav': False, 'carolteodori': False, 'thank': False, 'god': False, 'wa': False, 'almost': False, 'hehe': False, 'got': False, 'ebay': False, 'must': False, 'hat': False, 'sore': False, 'lip': False, 'tongu': False, 'throat': False, 'amp': False, 'tooth': False, 'next': False

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'s': False, 'kinda': False, 'mad': False, 'though': False, 'enjoy': False, 'day': False, 'work': False, 'hard': False, 'im': False, 'busi': False, 'have': False, 'lot': False, 'thing': False, 'do': False, 'gnite': False, 'twitter': False, 'hr': False, 'raniinsight': False, 'hey': False, 'rani': False, 'coley': False, 'sweet': False, 'carbon': False, 'like': False, 'lol': False, 'awak': False, 'sick': False, 'realli': False, 'speroamor': False, 'noia': False, 'oh': False, 'dear': False, 'lord': False, 'hell': False, 'i': False, 'gon': False, 'na': False, 'cool': False, 'bonasauru': False, 'whi': True, 't': False, 'peopl': False, 'appreci': False, 'static': False, 'type': False, 'emmaaaar': False, 'sound': False, 'laaaav': False, 'carolteodori': False, 'thank': False, 'god': False, 'wa': False, 'almost': False, 'hehe': False, 'got': False, 'ebay': False, 'must': False, 'hat': False, 'sore': False, 'lip': False, 'tongu': False, 'throat': False, 'amp': False, 'tooth': False, 'next': False

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'s': False, 'kinda': False, 'mad': False, 'though': False, 'enjoy': False, 'day': False, 'work': False, 'hard': False, 'im': False, 'busi': False, 'have': False, 'lot': False, 'thing': False, 'do': False, 'gnite': False, 'twitter': False, 'hr': False, 'raniinsight': False, 'hey': False, 'rani': False, 'coley': False, 'sweet': False, 'carbon': False, 'like': False, 'lol': False, 'awak': False, 'sick': False, 'realli': False, 'speroamor': False, 'noia': False, 'oh': False, 'dear': False, 'lord': False, 'hell': False, 'i': False, 'gon': False, 'na': False, 'cool': False, 'bonasauru': False, 'whi': False, 't': False, 'peopl': False, 'appreci': False, 'static': False, 'type': False, 'emmaaaar': False, 'sound': False, 'laaaav': False, 'carolteodori': False, 'thank': False, 'god': False, 'wa': False, 'almost': False, 'hehe': False, 'got': False, 'ebay': False, 'must': False, 'hat': False, 'sore': False, 'lip': False, 'tongu': False, 'throat': False, 'amp': False, 'tooth': False, 'next': Fals

### Building and Traininng Naive Bayes Model

In this step you will split your feature set into a training and a test set. Then you will create a Bayes classifier instance using `nltk.NaiveBayesClassifier.train` ([example](https://www.nltk.org/book/ch06.html)) to train with the training dataset.

After training the model, call `classifier.show_most_informative_features()` to inspect the most important features. The output will look like:

```
Most Informative Features
	    snow = True            False : True   =     34.3 : 1.0
	  easter = True            False : True   =     26.2 : 1.0
	 headach = True            False : True   =     20.9 : 1.0
	    argh = True            False : True   =     17.6 : 1.0
	unfortun = True            False : True   =     16.9 : 1.0
	    jona = True             True : False  =     16.2 : 1.0
	     ach = True            False : True   =     14.9 : 1.0
	     sad = True            False : True   =     13.0 : 1.0
	  parent = True            False : True   =     12.9 : 1.0
	  spring = True            False : True   =     12.7 : 1.0
```

The [following video](https://www.youtube.com/watch?v=rISOsUaTrO4) will help you complete this step. The source code in this video can be found [here](https://pythonprogramming.net/naive-bayes-classifier-nltk-tutorial/).

[![Building and Training NB](nb-model-building.jpg)](https://www.youtube.com/watch?v=rISOsUaTrO4)

In [18]:
import nltk
import random

random.shuffle(feature_set)
train_set = feature_set[:8000]
test_set = feature_set[8000:]

classifier = nltk.NaiveBayesClassifier.train(train_set)

classifier.show_most_informative_features()

accuracy = nltk.classify.accuracy(classifier, test_set)
print("Classifier Accuracy:", accuracy)

Most Informative Features
                     sad = True                0 : 4      =     22.2 : 1.0
                     ugh = True                0 : 4      =     19.1 : 1.0
                  welcom = True                4 : 0      =     16.3 : 1.0
                    pain = True                0 : 4      =     13.1 : 1.0
                    poor = True                0 : 4      =     13.1 : 1.0
            followfriday = True                4 : 0      =     12.3 : 1.0
                    crap = True                0 : 4      =     11.7 : 1.0
                   upset = True                0 : 4      =     11.7 : 1.0
                    sore = True                0 : 4      =     11.0 : 1.0
                     cri = True                0 : 4      =     10.7 : 1.0
Classifier Accuracy: 0.7264166666666667


### Testing Naive Bayes Model

Now we'll test our classifier with the test dataset. This is done by calling `nltk.classify.accuracy(classifier, test)`.

As mentioned in one of the tutorial videos, a Naive Bayes model is considered OK if your accuracy score is over 0.6. If your accuracy score is over 0.7, you've done a great job!

In [19]:
accuracy = nltk.classify.accuracy(classifier, test_set)
print("Classifier Accuracy:", accuracy)

Classifier Accuracy: 0.7264166666666667


## Bonus Question 1: Improve Model Performance

If you are still not exhausted so far and want to dig deeper, try to improve your classifier performance. There are many aspects you can dig into, for example:

* Improve stemming and lemmatization. Inspect your bag of words and the most important features. Are there any words you should furuther remove from analysis? You can append these words to further remove to the stop words list.

* Remember we only used the top 5,000 features to build model? Try using different numbers of top features. The bottom line is to use as few features as you can without compromising your model performance. The fewer features you select into your model, the faster your model is trained. Then you can use a larger sample size to improve your model accuracy score.

In [ ]:
# your code here

## Bonus Question 2: Machine Learning Pipeline

In a new Jupyter Notebook, combine all your codes into a function (or a class). Your new function will execute the complete machine learning pipeline job by receiving the dataset location and output the classifier. This will allow you to use your function to predict the sentiment of any tweet in real time. 

In [ ]:
# your code here

## Bonus Question 3: Apache Spark

If you have completed the Apache Spark advanced topic lab, what you can do is to migrate your pipeline from local to a Databricks Notebook. Share your notebook with your instructor and classmates to show off your achievements!

In [ ]:
# your code here